In [1]:
!pip install tensorflow==2.0

In [0]:
!pip install -q tensorflow-datasets

In [3]:
# NOTE: PLEASE MAKE SURE YOU ARE RUNNING THIS IN A PYTHON3 ENVIRONMENT

import tensorflow as tf
print(tf.__version__)

# This is needed for the iterator over the data
# But not necessary if you have TF 2.0 installed
#!pip install tensorflow==2.0.0-beta0

# !pip install -q tensorflow-datasets

2.0.0


In [4]:
import tensorflow_datasets as tfds
imdb, info = tfds.load("imdb_reviews", with_info=True, as_supervised=True)


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


Dataset imdb_reviews downloaded and prepared to /root/tensorflow_datasets/imdb_reviews/plain_text/0.1.0. Subsequent calls will reuse this data.


In [0]:
import numpy as np

train_data, test_data = imdb['train'], imdb['test']

training_sentences = []
training_labels = []

testing_sentences = []
testing_labels = []

In [10]:
info

tfds.core.DatasetInfo(
    name='imdb_reviews',
    version=0.1.0,
    description='Large Movie Review Dataset.
This is a dataset for binary sentiment classification containing substantially more data than previous benchmark datasets. We provide a set of 25,000 highly polar movie reviews for training, and 25,000 for testing. There is additional unlabeled data for use as well.',
    urls=['http://ai.stanford.edu/~amaas/data/sentiment/'],
    features=FeaturesDict({
        'label': ClassLabel(shape=(), dtype=tf.int64, num_classes=2),
        'text': Text(shape=(), dtype=tf.string),
    }),
    total_num_examples=100000,
    splits={
        'test': 25000,
        'train': 25000,
        'unsupervised': 50000,
    },
    supervised_keys=('text', 'label'),
    citation="""@InProceedings{maas-EtAl:2011:ACL-HLT2011,
      author    = {Maas, Andrew L.  and  Daly, Raymond E.  and  Pham, Peter T.  and  Huang, Dan  and  Ng, Andrew Y.  and  Potts, Christopher},
      title     = {Learning Word V

In [0]:
# str(s.tonumpy()) is needed in Python3 instead of just s.numpy()
for s,l in train_data:
  training_sentences.append(str(s.numpy()))
  training_labels.append(l.numpy())
  
for s,l in test_data:
  testing_sentences.append(str(s.numpy()))
  testing_labels.append(l.numpy())
  
training_labels_final = np.array(training_labels) # list -> array
testing_labels_final = np.array(testing_labels)


In [0]:
vocab_size = 10_000
embedding_dim = 16
max_length = 120
trunc_type='post'
oov_tok = "<OOV>"


from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

tokenizer = Tokenizer(num_words=vocab_size, oov_token=oov_tok)
tokenizer.fit_on_texts(training_sentences)
word_index = tokenizer.word_index
sequences = tokenizer.texts_to_sequences(training_sentences)
padded = pad_sequences(sequences,maxlen=max_length, truncating=trunc_type)

testing_sequences = tokenizer.texts_to_sequences(testing_sentences)
testing_padded = pad_sequences(testing_sequences,maxlen=max_length)



In [18]:
len(word_index)

86539

In [22]:
len(padded[2])

120

In [19]:
reverse_word_index = dict([(value, key) for (key, value) in word_index.items()])

def decode_review(text):
    return ' '.join([reverse_word_index.get(i, '?') for i in text])

print(decode_review(padded[1]))
print(training_sentences[1])

<OOV> gable plays a con man who <OOV> into the life of hard boiled dame jean harlow he tries to sucker her while she <OOV> him off with her tough gal attitude despite their cynicism and cons they fall in love when gable accidentally kills a man during a <OOV> he runs out leaving loyal harlow to women 's prison where she discovers she 's pregnant anita <OOV> ' and howard <OOV> rogers ' writing is excellent throughout with many well drawn and surprising characters including a jewish socialist woman <OOV> and a black woman <OOV> and her preacher father played with hardly a trace of stereotype gable and harlow show their <OOV> as actors adding telling nuances and quirks
b'Clark Gable plays a con man who busts into the life of hard-boiled dame Jean Harlow. He tries to sucker her while she brushes him off with her tough-gal attitude. Despite their cynicism and cons they fall in love. When Gable accidentally kills a man during a sting he runs out leaving loyal Harlow to women\'s prison where 

In [26]:
model = tf.keras.Sequential([
    tf.keras.layers.Embedding(vocab_size, embedding_dim, input_length=max_length),
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(6, activation='relu'),
    tf.keras.layers.Dense(1, activation='sigmoid')
])
model.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy'])
model.summary()


Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, 120, 16)           160000    
_________________________________________________________________
flatten (Flatten)            (None, 1920)              0         
_________________________________________________________________
dense (Dense)                (None, 6)                 11526     
_________________________________________________________________
dense_1 (Dense)              (None, 1)                 7         
Total params: 171,533
Trainable params: 171,533
Non-trainable params: 0
_________________________________________________________________


In [27]:
num_epochs = 10
model.fit(padded, training_labels_final, epochs=num_epochs, validation_data=(testing_padded, testing_labels_final))

Train on 25000 samples, validate on 25000 samples
Epoch 1/10
25000/25000 [==============================] - 6s 240us/sample - loss: 0.4996 - accuracy: 0.7366 - val_loss: 0.3471 - val_accuracy: 0.8488
Epoch 2/10
25000/25000 [==============================] - 5s 212us/sample - loss: 0.2416 - accuracy: 0.9068 - val_loss: 0.3726 - val_accuracy: 0.8382
Epoch 3/10
25000/25000 [==============================] - 5s 212us/sample - loss: 0.0923 - accuracy: 0.9764 - val_loss: 0.4534 - val_accuracy: 0.8238
Epoch 4/10
25000/25000 [==============================] - 5s 201us/sample - loss: 0.0231 - accuracy: 0.9972 - val_loss: 0.5276 - val_accuracy: 0.8246
Epoch 5/10
25000/25000 [==============================] - 5s 202us/sample - loss: 0.0067 - accuracy: 0.9995 - val_loss: 0.5923 - val_accuracy: 0.8241
Epoch 6/10
25000/25000 [==============================] - 5s 203us/sample - loss: 0.0023 - accuracy: 0.9999 - val_loss: 0.6468 - val_accuracy: 0.8239
Epoch 7/10
25000/25000 [==========================

In [28]:
e = model.layers[0]
weights = e.get_weights()[0]
print(weights.shape) # shape: (vocab_size, embedding_dim)

(10000, 16)


In [0]:
import io

out_v = io.open('vecs.tsv', 'w', encoding='utf-8')
out_m = io.open('meta.tsv', 'w', encoding='utf-8')
for word_num in range(1, vocab_size):
  word = reverse_word_index[word_num]
  embeddings = weights[word_num]
  out_m.write(word + "\n")
  out_v.write('\t'.join([str(x) for x in embeddings]) + "\n")
out_v.close()
out_m.close()

In [0]:

try:
  from google.colab import files
except ImportError:
  pass
else:
  files.download('vecs.tsv')
  files.download('meta.tsv')

In [32]:
sentence = "I really think this is amazing. honest."
sequence = tokenizer.texts_to_sequences(sentence)
print(sequence)

[[11], [], [1431], [969], [4], [1538], [1538], [4740], [], [790], [2014], [11], [2925], [2188], [], [790], [2014], [11], [579], [], [11], [579], [], [4], [1781], [4], [4510], [11], [2925], [1279], [], [], [2014], [1005], [2925], [969], [579], [790], []]


In [0]:
tokenizer.get_config()

{'char_level': False,
 'document_count': 25000,
 'filters': '!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n',
 'index_docs': '{"113": 4597, "2521": 196, "174": 3069, "659": 872, "2": 24787, "79": 6757, "4413": 97, "2193": 226, "14395": 17, "216": 2743, "167": 3384, "19": 17976, "92": 6496, "15494": 15, "6": 23474, "1443": 367, "10": 21773, "391": 1535, "344": 1594, "25011": 6, "356": 1637, "29": 14139, "105": 5438, "2297": 203, "4518": 92, "8": 14666, "62": 8408, "434": 1281, "395": 1438, "284": 1965, "16": 17865, "466": 1278, "175": 3284, "33": 11718, "502": 1125, "20": 13899, "3677": 113, "17588": 12, "386": 1442, "254": 2297, "9": 22026, "644": 875, "5": 23724, "30": 14094, "127": 4795, "392": 1595, "319": 1660, "55": 8930, "135": 4104, "91": 6280, "280": 1971, "443": 1292, "5740": 67, "13": 20165, "625": 892, "3": 24164, "7": 22426, "82": 6185, "11": 19381, "278": 1941, "150": 3701, "111": 5329, "28": 14183, "116": 5354, "250": 2365, "422": 1354, "51": 9718, "1050": 555, "12": 22357, "251": 